<a href="https://www.kaggle.com/code/lccburk/cdr-forecasting?scriptVersionId=151752680" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

I recently joined the team over at [CDR.fyi](www.cdr.fyi), a website started in 2022 that has since become the largest open data platform dedicated to high-permanence CDR monitoring. My first project with the team was to build a forecasting model from scratch to predict CDR orders and deliveries.

### Forecasting total purchased and delivered
**Goal**: Develop a model to forecast CDR order and delivery volume.  
**Approach**: Use the [Darts](https://unit8co.github.io/darts/) library to import the cumulative purchased and delivered totals as a time series and test out a variety of built in forecasting models. Darts offers a few probabilistic models out of the box which we can use to get a forecast range along with a variety of metrics we can use to quantify their performance on historical data.
- **Attempt #1: Linear Regression Model**: Simple, easy to interpret, and supports probabilistic forecasting. We forecast ahead based on a linear regression of a set number of previous values. This model didn't work well in the end because I found it to be too unstable and sensitive to training range. Also, it does not support monotonic constraints and is prone to oscillations, not great. 
- **Attempt #2: XGBoost**: Darts also supports XGBoost forecasting, which supports both probabilistic forecasting and monotonic constraints. However no matter how much I fiddled with the parameters I was never able to get decent forecasts out of this method. Maybe someone else has some ideas on how to get better results with xgb? This is the only out-of-the-box Darts forecasting approach I'm aware of that offers both monotonic constraints and probabilistic forecasting, so I had to move on to a different approach.
- **Attempt #3: Monte Carlo/Stochastic modeling**: We model our function as a [compound Poisson process](https://en.wikipedia.org/wiki/Compound_Poisson_process) that has the same statistical properties as our functions of interest, and then numerically simulate it a bunch of times. This ended up giving me the best results and has some nice properties - it's pretty simple to understand and interpret, it allows us to set confidence intervals, its forecasts are all monotonically increasing, and it looks good in a graph. 

#### More on the model
Right now the model is pretty simple: 
- The probability of there being a jump (purchase or delivery) at a given time-step will be given by the average jump probability for the training set, i.e. (# of jumps)/(# of steps)
- The size of the jump will be selected from a distribution fitted to the (log) jump sizes from the training set. 

To create a forecast, we fit our stochastic model to the previous data, then run it a bunch of times to generate lots of potential trajectories. We can then take the median value of all the trajectories at each time step to get a forecast of the 'most likely' future path.

In [1]:
# Installing darts
!pip install darts

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 814.3/814.3 kB 16.3 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 54.1 MB/s eta 0:00:00:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 160.5/160.5 kB 12.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.9/110.9 kB 10.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.0/44.0 kB 3.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 279.8/279.8 kB 21.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.2/169.2 kB 14.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.7/154.7 kB 9.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 144.2/144.2 kB 12.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.3/135.3 kB 12.9 MB/s eta 0:00:00
  Created wheel for 

In [2]:
# Importing packages and preparing time series for forecasting
import pandas as pd 
import numpy as np
import matplotlib.pyplot as plt

import darts 
from darts import TimeSeries 
from darts.metrics import mape, mase, quantile_loss, rho_risk
import datetime as dt 

from scipy.stats import norm, skewnorm, gaussian_kde, levy_stable, normaltest
from sklearn.neighbors import KernelDensity

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots 

pd.set_option('display.max_column', None)

In [3]:
# Load CDR orders dataset
orders_df = pd.read_csv('/kaggle/input/cdr-marketwatch-orders/code 7_2023-10-31T1344.csv').sort_values(by='created_at')

In [4]:
def make_timeseries(orders_df, include_loimou=True) :
    df = orders_df.sort_values(by='created_at')

    if not include_loimou :
        df = df[df['status'] != 'LOI/MOU']

    start = pd.to_datetime(df.created_at, format='ISO8601').dt.tz_localize(None).min().replace(hour=0, minute=0, second=0, microsecond=0)
    end = pd.to_datetime(df.created_at, format='ISO8601').dt.tz_localize(None).max().replace(hour=0, minute=0, second=0, microsecond=0)

    dates = [start + dt.timedelta(d) for d in range(1, (end-start).days+2)]
    purchased = np.array([df[pd.to_datetime(df['created_at'], format='ISO8601').dt.tz_localize(None) < date]['tons_purchased'].sum().astype(pd.Float32Dtype) for date in dates])
    delivered = np.array([df[pd.to_datetime(df['created_at'], format='ISO8601').dt.tz_localize(None) < date]['tons_delivered'].sum().astype(pd.Float32Dtype) for date in dates])

    data = pd.DataFrame()
    data['date'] = dates
    data['total_purchased'] = purchased
    data['total_delivered'] = delivered

    ts = TimeSeries.from_dataframe(data, time_col='date', value_cols=['total_purchased', 'total_delivered'])

    return ts

ts = make_timeseries(orders_df, include_loimou=False)
ts_with_loimou = make_timeseries(orders_df, include_loimou=True)

## Creating forecasts and plots

In [5]:
def Forecast(ts, col, n_days=365, n_samples=1000, fit_type='auto', min_diff=1/2000, make_fig=True, plot_fig=True, confidence_interval=90, verbose=False, show_sample_paths=False, validation_series=None, fig_template='simple_white', fig_label=None, remove_outliers=False, plot_hist=False, plot_2050_goal=False) : 
    '''
    Forecasting parameters: 
    ts : A Darts time series containing total_purchased and total_delivered values
    col : One of either 'total_purchased' or 'total_delivered'
    n_days : Number of days to forecast ahead
    n_samples : Number of sample trajectories used in simulation
    fit_type : Type of distribution to use for jump size. Current options are 'gaussian', 'kde', 'skewnorm', 'gaussian_kde', 'levy_stable' or 'auto'. Auto chooses between gaussian and kde based on normaltest value. Note that 'levy_stable' can have significantly slower performance than the others.
    min_diff : Minimum jump size cutoff, in tons. Extremely small orders/deliveries can skew the normal distribution fit. Default is 1 lb.
    
    Plotting parameters: 
    plot_forecast : If False then only return the forecast timeseries without plotting the result.
    confidence_interval : Either None or a number in range (0, 100], determines size of confidence/percentile interval in the plot.
    show_sample_paths : If True all sample paths are plotted (may be slow). If False, none are plotted. If int > 1 denotes the number of paths to be plotted.
    validation_series : Either None or a Darts time series containing total_purchased and total_delivered values to be plotted alongside forecast. If provided, metrics will be printed as well quantifying prediction fit.
    fig_template : A valid plotly template. See: https://plotly.com/python/templates/
    remove_outliers : Fit jump size distribution using only jumps within one standard deviation of mean jump size. Tends to result in underestimates. 
    verbose : Print distribution fit and backtesting metrics.
    plot_hist : Plot a histogram of log(purchase/delivery sizes) along with fitted normal distribution used by model
    plot_2050_goal : Plots an exponential curve from the current value to 10 gigatons in 2050.
    '''
    ### FORECASTING ###
    # Get series of interest
    series = ts[col]

    # Use diff to get individual purchases/deliveries
    diffs = series.diff().values().flatten()
    
    # Only consider purchases/deliveries greater than cutoff (could skew distribution otherwise)
    positive_diffs = diffs[np.where(diffs > min_diff)]
    
    # Get jump probability 
    jump_prob = sum(diffs > min_diff) / len(diffs)

    # Get normality probability 
    if verbose or (fit_type=='auto') :
        _, pvalue = normaltest(np.log(positive_diffs))
    
    if verbose: 
        print('Simulating:')
        print(f'     Normality likelihood: {100*pvalue:.2f}%')
    
    # If fit_type is auto, assign based on normality probability
    if fit_type == 'auto' : 
        fit_type = 'gaussian' if pvalue > 0.5 else 'kde'
    
    # Fitting chosen distribution to jump size data
    if fit_type=='gaussian' : 
        mu, sigma = norm.fit(np.log(positive_diffs))
        
    elif fit_type=='kde' : 
        kde = KernelDensity(kernel='gaussian', bandwidth=1).fit(np.log(positive_diffs).reshape((-1,1)))
        
    elif fit_type=='skewnorm' : 
        a, loc, scale = skewnorm.fit(np.log(positive_diffs))
        
    elif fit_type=='gaussian_kde' :
        gkde = gaussian_kde(np.log(positive_diffs))
        
    elif fit_type=='levy_stable' : 
        fit_params = levy_stable.fit(np.log(positive_diffs))
        
    else : 
        raise ValueError('Invalid fit type given.')
        
    # Want to forecast at least 365 days ahead to get year ahead forecast
    n_forecast = max(n_days, 365)

    # Generating sample paths using average jump likelihood and fitted log(jump size) distribution
    initial_value = series.values().flatten()[-1]

    if fit_type=='gaussian' : 
        jumps = np.exp(np.random.normal(mu, sigma, (n_forecast, n_samples))) * (np.random.random((n_forecast, n_samples)) <= jump_prob)
        
    elif fit_type=='kde' : 
        jumps = np.exp(kde.sample((n_forecast, n_samples)).squeeze()) * (np.random.random((n_forecast, n_samples)) <= jump_prob)
        
    elif fit_type=='skewnorm' : 
        jumps = np.exp(skewnorm.rvs(a, loc, scale, (n_forecast, n_samples))) * (np.random.random((n_forecast, n_samples)) <= jump_prob)
        
    elif fit_type=='gaussian_kde' : 
        jumps = np.exp(gkde.resample(n_forecast * n_samples).reshape((n_forecast, n_samples))) * (np.random.random((n_forecast, n_samples)) <= jump_prob)
        
    elif fit_type=='levy_stable' : 
        jumps = np.exp(levy_stable.rvs(*fit_params, (n_forecast, n_samples))) * (np.random.random((n_forecast, n_samples)) <= jump_prob)

    # Getting sample paths from jump data and converting to Darts stochastic TimeSeries object
    sample_paths = np.cumsum(jumps, axis=0).reshape(n_forecast, 1, n_samples) + initial_value
    dates = pd.DatetimeIndex([ts.end_time() + dt.timedelta(days=d+1) for d in range(n_forecast)])
    forecast = TimeSeries.from_times_and_values(dates, sample_paths)
    
    # Getting low and high percentile trajectories
    if confidence_interval != None : 
        low_percentile = forecast.quantile((50-confidence_interval/2)/100).values().flatten()
        high_percentile = forecast.quantile((50+confidence_interval/2)/100).values().flatten()

    # Get median path 
    median_path = forecast.median().values().flatten()

    # Producing month ahead, year ahead, EOY, and end of forecast predictions from median path
    if verbose : 
        forecast_periods = {
            'Month ahead' : int(median_path[29]), 
            'Year ahead' : int(median_path[364]),
            'End of year' : int(median_path[(dt.datetime(year=ts.end_time().year, month=12, day=31) - ts.end_time()).days]), 
            'End of forecast' : int(median_path[n_days-1])
        }

        print("\nForecast periods:")
        for key, val in forecast_periods.items() : 
            print(f"     {key}: {int(val)} Tons")

    # If not plot_forecast, simply return the forecast, otherwise, continue to plotting
    if make_fig == False : 
        return forecast

    ### PLOTTING ###
    # Making plotly figure
    fig = make_subplots(rows=2, cols=1, row_heights=[0.7, 0.3]) if plot_hist else make_subplots(rows=1, cols=1)

    # Get name of quantity from dict for plots
    quantity_name = {'total_purchased': 'Purchases', 'total_delivered': 'Deliveries'}[col]

    # Defining forecast dates for plotting
    forecast_dates = series.time_index[[-1]].union(forecast.time_index[:n_days])
    
    # Add trace for total purchases
    fig.add_trace(go.Scatter(
        x=series.time_index, 
        y=series.values().flatten(), 
        mode='lines', 
        name=f'Total {quantity_name}', 
        legendrank=1
    ))
    
    # Add trace for each simulated trajectory
    if show_sample_paths : 
        # If show_sample_paths is an integer > 1 then interpret it as maximum number of sample plots
        max_sample_plots = show_sample_paths if (show_sample_paths > 1) else -1
        
        sample_paths = np.squeeze(forecast.all_values()).T
        for path in sample_paths[:max_sample_plots]:
            if (confidence_interval==None) or (low_percentile[n_days-1] <= path[n_days-1] <= high_percentile[n_days-1]) : 
                fig.add_trace(go.Scatter(
                    x=forecast_dates, 
                    y=np.insert(path, 0, initial_value), 
                    mode='lines', 
                    line=dict(color='gray', width=1), 
                    opacity=0.1, 
                    showlegend=False, 
                    hoverinfo='skip'
                ), 
                row=1, col=1)
                
    # Plotting confidence interval
    if confidence_interval != None : 
        # Add trace for the high percentile path
        fig.add_trace(go.Scatter(
            x=forecast_dates, 
            y=np.insert(high_percentile, 0, initial_value), 
            mode='lines', 
            line=dict(color='rgba(0,0,0,0)'),
            showlegend=False,
            hoverinfo='skip'
        ), 
        row=1, col=1)

        # Add trace for the low percentile path with fill
        fig.add_trace(go.Scatter(
            x=forecast_dates, 
            y=np.insert(low_percentile, 0, initial_value), 
            mode='lines', 
            fill='tonexty',  # fill area between low percentile and high percentile trace
            line=dict(color='gray'),
            opacity=0.01,
            name=f'{confidence_interval}% Confidence',
            showlegend=True,
            legendrank=4,
            hoverinfo='skip'
        ),
        row=1, col=1)

    # Add trace for validation series, if provided
    if validation_series != None : 
        val_series = validation_series[col]
        fig.add_trace(go.Scatter(
            x=series.time_index[[-1]].union(val_series.time_index), 
            y=np.insert(val_series.values().flatten(), 0, initial_value), 
            mode='lines', 
            line=dict(color='orange'),
            name=f'Total {quantity_name} (Validation)',
            legendrank=2
        ), 
        row=1, col=1)

        if verbose : 
            print('\nValidating: ')
            print(f"     Mean Absolute Percentage Error: {mape(val_series, forecast[:n_days]):.2f}%")

            print(f"     Mean Absolute Scaled Error: {mase(val_series[:n_days], forecast[:n_days], series):.2f}")
        
            if confidence_interval : 
                print(f"     Quantile Loss: {quantile_loss(val_series, forecast[:n_days], tau=(50-confidence_interval/2)/100):.2f}")

                print(f"     ρ-Risk: {rho_risk(val_series, forecast[:n_days], rho=(50-confidence_interval/2)/100):.2f}")
    
    # Add trace for the median path
    fig.add_trace(go.Scatter(
        x=forecast_dates, 
        y=np.insert(median_path, 0, initial_value), 
        mode='lines', 
        line=dict(color='red'), 
        name=f'Projected {quantity_name}',
        legendrank=3
    ), 
    row=1, col=1)
    
    # Plotting histogram, if applicable
    if plot_hist : 
        
        # Plot training set histogram
        n_bins = int(np.ceil(np.log(positive_diffs).max()) - np.floor(np.log(positive_diffs).min()))
        fig.add_trace(go.Histogram(
            x=np.log(positive_diffs), 
            nbinsx=n_bins, 
            histnorm='probability', 
            marker=dict(color='gray'),
            showlegend=False
        ), 
        row=2, col=1)
        
        # Plot fitted distribution
        xrange = np.linspace(np.log(positive_diffs).min()-1, np.log(positive_diffs).max()+1, 1000)
        if fit_type=='gaussian' : 
            yvals = norm.pdf(xrange, mu, sigma)
            
        elif fit_type=='kde' :
            yvals = np.exp(kde.score_samples(xrange.reshape((-1,1))))
            
        elif fit_type=='skewnorm' : 
            yvals = skewnorm.pdf(xrange, a, loc, scale)
            
        elif fit_type=='gaussian_kde' :
            yvals = gkde.pdf(xrange)
            
        elif fit_type=='levy_stable' : 
            yvals = levy_stable.pdf(xrange, *fit_params)
        
        fig.add_trace(go.Scatter(
            x=xrange, 
            y=yvals, 
            mode='lines', 
            line=dict(color='red'),
            name=None, 
            showlegend=False
        ), 
        row=2, col=1)
        
        # Format histogram
        quantity_name_singular = {'total_purchased': 'Purchase', 'total_delivered': 'Delivery'}[col]
        fig.update_layout(
            xaxis2_title=f'log({quantity_name_singular} Size)', 
            xaxis2_dtick=1, 
            yaxis2_tickformat='.0%'
        )
    
    # Plot exponential trajectory to 10GTons in 2050, if applicable
    if plot_2050_goal : 
        days_to_2050 = (dt.datetime(year=2050, month=1, day=1) - ts.time_index[-1]).days

        y0 = float(series.values()[-1])
        b = (10 * np.log(10) - np.log(y0))/days_to_2050
        f = lambda x : y0 * np.exp(b * x)
        
        xrange = np.arange(days_to_2050+1)
        dates = [ts.time_index[-1] + dt.timedelta(days=int(d)) for d in xrange]
        
        fig.add_trace(go.Scatter(
            x=dates, 
            y=f(xrange), 
            name='2050 Goal Trajectory',
            line=dict(color='gold', dash='dot'), 
            opacity=0.5
        ),
        row=1, col=1)
        
    
    # Update layout, add theme and titles
    fig_label = f"<br><sub>{fig_label}<sub>" if fig_label else ""
    t0, tf = dt.datetime.strftime(series.time_index[0], '%Y-%m-%d'), dt.datetime.strftime(forecast_dates[-1], '%Y-%m-%d')
    fig.update_layout(
        yaxis_range = [0,high_percentile[n_days-1]],
        xaxis_range = [t0, tf],
        title_text = f"Total {quantity_name}" + fig_label,
        margin_autoexpand=True,
        yaxis_title = "Tons of CO₂",
        legend_traceorder="normal",
        template=fig_template
    )
    
    # Show figure
    if plot_fig : 
        fig.show()

    return forecast, fig


### Forecasting Purchases and Deliveries

In [6]:
# Forecasting purchases and deliveries
training, validation = ts.split_before(pd.Timestamp(year=2023, month=7, day=1))

params = dict(
    ts=training,
    n_days=max(len(validation), 365),
    n_samples=10000, 
    min_diff=1/2000,
    confidence_interval=50, 
    show_sample_paths=250, 
    fit_type='gaussian_kde',
    validation_series=validation,
    verbose=True, 
    plot_fig=True,
    plot_hist=False,
    plot_2050_goal=True
)

for quantity, quantity_name in zip(['total_purchased', 'total_delivered'], ['Total Purchases', 'Total Deliveries']) : 
    print(f"\n--- {quantity_name} Forecast ---")
    Forecast(
        col=quantity,
        **params
    )


--- Total Purchases Forecast ---
Simulating:
     Normality likelihood: 61.82%

Forecast periods:
     Month ahead: 4070927 Tons
     Year ahead: 7783088 Tons
     End of year: 5231007 Tons
     End of forecast: 7783088 Tons

Validating: 
     Mean Absolute Percentage Error: 3.64%
     Mean Absolute Scaled Error: 17.96
     Quantile Loss: 1164625.81
     ρ-Risk: 0.02



--- Total Deliveries Forecast ---
Simulating:
     Normality likelihood: 27.37%

Forecast periods:
     Month ahead: 75488 Tons
     Year ahead: 195951 Tons
     End of year: 127854 Tons
     End of forecast: 195951 Tons

Validating: 
     Mean Absolute Percentage Error: 6.40%
     Mean Absolute Scaled Error: 34.55
     Quantile Loss: 12030.01
     ρ-Risk: 0.06


### Comparing results from different fitted distributions

In [7]:
# Comparing effect on forecast of using various distributions
training, validation = ts.split_before(pd.Timestamp(year=2023, month=7, day=1))

params = dict(
    ts=training,
    n_days=max(len(validation), 365),
    n_samples=1000, 
    min_diff=1/2000,
    confidence_interval=50, 
    show_sample_paths=0, 
    validation_series=validation,
    verbose=True, 
    plot_fig=False,
    plot_hist=True,
    plot_2050_goal=False, 
    fig_label='Distribution fit comparison'
)

for col in ['total_purchased', 'total_delivered'] : 
    # Making figures
    figs = []
    for fit_type, fig_label in zip(['kde', 'gaussian', 'skewnorm', 'gaussian_kde', 'levy_stable'], ['KDE', 'Gaussian', 'Skew Norm', 'Gaussian KDE', 'Levy Stable']) :
        
        print(f"\n--- {fig_label} Forecast ---")
        forecast, fig = Forecast(
            **params,
            col=col,
            fit_type=fit_type
            )

        figs.append(fig)

    fig_dict = {
        "data": [],
        "layout": figs[0].layout,
        "frames": []
    }

    ### Making animation ###
    # configure slider
    slider_dict = {
        "active": 0,
        "yanchor": "top",
        "xanchor": "left",
        "currentvalue": {
            "font": {"size": 14},
            "prefix": "Distribution: ",
            "visible": True,
            "xanchor": "right"
        },
        "transition": {"duration": 150, "easing": "linear"},
        "pad": {"b": 10, "t": 50},
        "len": 1.0,
        "x": 0,
        "y": 0,
        "steps": []
    }

    # make data 
    fig_dict["data"] = figs[0].data

    # make frames
    names = ['KDE', 'Gaussian', 'Skew Norm', 'Gaussian KDE', 'Levy Stable']
    for fig, name in zip(figs, names) : 
        frame = {'data': fig.data, 'name' : name}
        fig_dict["frames"].append(frame)

        slider_step = {"args": [
            [name],
            {"frame": {"duration": 1000, "redraw": True},
             "mode": "immediate",
             "transition": {"duration": 0, "easing": "linear"}}
        ],
            "label": name,
            "method": "animate"}
        slider_dict["steps"].append(slider_step)

    fig_dict["layout"]["sliders"] = [slider_dict]

    anim = go.Figure(fig_dict)

    anim.show()


--- KDE Forecast ---
Simulating:
     Normality likelihood: 61.82%

Forecast periods:
     Month ahead: 4057969 Tons
     Year ahead: 6669198 Tons
     End of year: 4810244 Tons
     End of forecast: 6669198 Tons

Validating: 
     Mean Absolute Percentage Error: 4.78%
     Mean Absolute Scaled Error: 24.06
     Quantile Loss: 605222.02
     ρ-Risk: 0.03

--- Gaussian Forecast ---
Simulating:
     Normality likelihood: 61.82%

Forecast periods:
     Month ahead: 4056863 Tons
     Year ahead: 6889027 Tons
     End of year: 5104804 Tons
     End of forecast: 6889027 Tons

Validating: 
     Mean Absolute Percentage Error: 3.90%
     Mean Absolute Scaled Error: 19.47
     Quantile Loss: 1140518.01
     ρ-Risk: 0.03

--- Skew Norm Forecast ---
Simulating:
     Normality likelihood: 61.82%

Forecast periods:
     Month ahead: 4058676 Tons
     Year ahead: 6180806 Tons
     End of year: 4881521 Tons
     End of forecast: 6180806 Tons

Validating: 
     Mean Absolute Percentage Error: 4.29%
 


--- KDE Forecast ---
Simulating:
     Normality likelihood: 27.37%

Forecast periods:
     Month ahead: 75848 Tons
     Year ahead: 175580 Tons
     End of year: 120565 Tons
     End of forecast: 175580 Tons

Validating: 
     Mean Absolute Percentage Error: 6.92%
     Mean Absolute Scaled Error: 38.26
     Quantile Loss: 8550.14
     ρ-Risk: 0.06

--- Gaussian Forecast ---
Simulating:
     Normality likelihood: 27.37%

Forecast periods:
     Month ahead: 74653 Tons
     Year ahead: 192905 Tons
     End of year: 118375 Tons
     End of forecast: 192905 Tons

Validating: 
     Mean Absolute Percentage Error: 7.66%
     Mean Absolute Scaled Error: 43.12
     Quantile Loss: 42069.25
     ρ-Risk: 0.07

--- Skew Norm Forecast ---
Simulating:
     Normality likelihood: 27.37%

Forecast periods:
     Month ahead: 74723 Tons
     Year ahead: 149167 Tons
     End of year: 108336 Tons
     End of forecast: 149167 Tons

Validating: 
     Mean Absolute Percentage Error: 8.46%
     Mean Absolute S

### Historical forecasts

In [ ]:
from tqdm import tqdm
# Visualizing historical forecasts
params = dict(
    n_samples=1000, 
    min_diff=1/2000,
    confidence_interval=90, 
    show_sample_paths=0, 
    fit_type='gaussian_kde',
    verbose=False, 
    plot_fig=False,
    plot_hist=True,
    plot_2050_goal=True,
    fig_label='Historical forecasts'
)

# Defining plot dates
start, end = dt.datetime(year=2022, month=10, day=1),  dt.datetime(year=2023, month=10, day=1)
dates = [pd.Timestamp(start + dt.timedelta(days=d)) for d in range((end-start).days + 1)]
dates = [date for date in dates if date.day in [1, 15]]

for col in ['total_purchased', 'total_delivered'] : 
    # Creating figures 
    figs = []
    days_to_2025 = (dt.datetime(year=2025, month=1, day=1) - ts.time_index[-1]).days + 1
    for date in tqdm(dates, desc=f'Forecasting {col}') : 
        training, validation = ts.split_before(date)

        _, fig = Forecast(
            ts=training, 
            col=col,
            validation_series=validation,
            n_days=len(validation) + days_to_2025,
            **params 
        )

        figs.append(fig)

    fig_dict = {
        "data": [],
        "layout": figs[0].layout,
        "frames": []
    }

    ### PLOTTING ###
    # Update axis bounds
    min_x, max_x = min([fig.layout.xaxis['range'][0] for fig in figs]), max([fig.layout.xaxis['range'][1] for fig in figs])
    min_y, max_y = min([fig.layout.yaxis['range'][0] for fig in figs]), validation[col].values().flatten()[-1] * 5

    fig_dict['layout'].xaxis['range'] = (min_x, max_x)
    fig_dict['layout'].yaxis['range'] = (min_y, max_y)

    # Adding buttons 
    fig_dict["layout"]["updatemenus"] = [
        {
            "buttons": [
                {
                    "args": [None, {"frame": {"duration": 250, "redraw": True},
                                    "fromcurrent": True, "transition": {"duration": 0,
                                                                        "easing": "elastic"}}],
                    "label": "⏵︎",
                    "method": "animate"
                },
                {
                    "args": [[None], {"frame": {"duration": 300, "redraw": False},
                                      "mode": "immediate",
                                      "transition": {"duration": 0}}],
                    "label": "⏸︎",
                    "method": "animate"
                }
            ],
            "direction": "left",
            "pad": {"r": 10, "t": 87},
            "showactive": False,
            "type": "buttons",
            "x": 0.1,
            "xanchor": "right",
            "y": 0.1,
            "yanchor": "top"
        }
    ]

    ### Making animation ###
    # configure slider
    slider_dict = {
        "active": 0,
        "yanchor": "top",
        "xanchor": "left",
        "currentvalue": {
            "font": {"size": 12},
            "prefix": "Forecast date: ",
            "visible": True,
            "xanchor": "right"
        },
        "transition": {"duration": 150, "easing": "linear"},
        "pad": {"b": 10, "t": 50},
        "len": 0.9,
        "x": 0.1,
        "y": 0,
        "steps": []
    }

    # make data 
    fig_dict["data"] = figs[0].data

    # make frames
    for fig, date in zip(figs, dates) : 
        datename = date.strftime("%b. %d, %Y")
        frame = {'data': fig.data, 'name' : datename}
        fig_dict["frames"].append(frame)

        slider_step = {"args": [
            [datename],
            {"frame": {"duration": 500, "redraw": True},
             "mode": "immediate",
             "transition": {"duration": 0, "easing": "elastic"}}
        ],
            "label": datename,
            "method": "animate"}
        slider_dict["steps"].append(slider_step)

    fig_dict["layout"]["sliders"] = [slider_dict]

    anim = go.Figure(fig_dict)

    anim.show()

### Predicting distribution evolution with DMD

In [ ]:
!pip install pydmd

In [ ]:
from pydmd import DMD 

In [ ]:
# making data 
start, end = dt.datetime(year=2022, month=10, day=1),  dt.datetime(year=2023, month=10, day=1)
dates = [pd.Timestamp(start + dt.timedelta(days=d)) for d in range((end-start).days + 1)]
dates = [date for date in dates if date.day in [1, 15]]

col = 'total_purchased'

dists = []

for date in dates : 
    n_days = (date - ts.time_index[0]).days
    diffs = ts[col][:n_days].diff().values().flatten()
    
    positive_diffs = diffs[np.where(diffs > 0)]
    
    dists.append(gaussian_kde(np.log(positive_diffs)))

xrange = np.linspace(-3, 20, 1000)

data = np.array([dist.pdf(xrange) for dist in dists])

dmd = DMD(svd_rank=0)
dmd.fit(data.T)

def predict_n(dmd, data, n) :
    A = data.sum()
    for _ in range(n) :
        data = dmd.predict(data)
        data = data * A / data.sum()
        
    return data

In [ ]:
cols = ['nframe', 'x', 'data']

plotdata = pd.DataFrame(columns=cols)
plotdata['nframe'] = [0] * len(xrange)
plotdata['x'] = xrange
plotdata['data'] = data[-1]

for nframe, X in enumerate(data) : 
    datapoint = pd.DataFrame(columns=cols)
    datapoint['nframe'] = [nframe] * len(xrange)
    datapoint['x'] = xrange
    datapoint['data'] = X
    
    plotdata = pd.concat([plotdata, datapoint])

nframes = 100
X, A = data[-1], data[-1].sum()
for nframe in range(1, nframes+1) : 
    X = dmd.predict(X)
    X = X * A / np.abs(X).sum()
    
    datapoint = pd.DataFrame(columns=cols)
    datapoint['nframe'] = [nframe + len(data)] * len(xrange)
    datapoint['x'] = xrange
    datapoint['data'] = X
    
    plotdata = pd.concat([plotdata, datapoint])

plotdata['data'] = np.abs(plotdata['data'])
px.line(plotdata, x='x', y='data', animation_frame='nframe')

In [ ]:
p = lambda f : lambda x: f(x)**2

In [ ]:
plt.plot(xrange[:-2], np.diff(dists[0].pdf(xrange), 2))

In [ ]:
plt.plot(xrange, np.sqrt(data[-1]))

In [ ]:
A 